In [13]:
## Import

from PIL import Image
import matplotlib.pyplot as plt
import tensorflow as tf
import pandas as pd
import numpy as np
import random
import cv2
import os

from tensorflow import keras
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout
from tensorflow.keras.utils import to_categorical

from datetime import datetime

In [3]:
## Helper functions

def read_from_folder(directory, input_shape):
    input = np.empty(input_shape, dtype='uint8')
    image_count = 0

    for filename in os.listdir(directory):
        f = os.path.join(directory, filename)
        if os.path.isfile(f) and (f.endswith('.jpg') or f.endswith('.jpeg')):
            img = Image.open(f)
    
            # Resize
            size = 176, 100
            img = img.resize(size, Image.LANCZOS)
    
            numpydata = np.array(img)
            input[image_count] = numpydata
    
            image_count += 1
    
            if image_count == 37:
                break  # Stop processing if 37 images are reached
    
    while image_count < 37:
        input[image_count] = input[image_count - 1]
        image_count += 1
    
    return input

def get_csv_dict(directory, labels, desired_rows):
    data = pd.read_csv(directory)
    data_dict = {i: [] for i in labels}
    
    for label in labels:
        filtered_data = data[data['label_id'].isin([label])]

        if len(filtered_data) >= desired_rows:
            data_dict[label] =  filtered_data['video_id'].values[:desired_rows]
            continue
    
        rows_to_add = desired_rows - len(filtered_data)
        random_rows = filtered_data.sample(n=rows_to_add, replace=True)
        data_dict[label] = pd.concat([filtered_data, random_rows], ignore_index=True)['video_id'].values

    return data_dict
        
def generate_data_labels(labels, label, length):
    data_label = []
    for i in range(length):
        result = [1 if labels[j] == label else 0 for j in range(len(labels))]
        data_label.append(result)
    return np.array(data_label)

def get_batch(directory, data_dict, chosen_labels, label, amount, index):    
    data = np.array([])

    for i in range(index, (index+amount)):
        example = read_from_folder(f"{directory}/{data_dict[label][i]}", (37, 100, 176, 3))
        example = np.expand_dims(example, axis=0)
        data = append_or_copy_array(data, example)
    
    #data = read_from_file(data_directory + "data" + "_batch_" + str(batch_num) + ".npy")
    data_labels = generate_data_labels(chosen_labels, label, len(data))
    
    return data, data_labels

def append_or_copy_array(base_array, new_array):
    if base_array.size == 0:
        result_array = new_array
    else:
        result_array = np.concatenate((base_array, new_array), axis=0)

    return result_array

def load_model_names(log_file):
    model_names = set()

    if os.path.exists(log_file):
        with open(log_file, 'r') as file:
            model_names = set(file.read().splitlines())

    return model_names

def cleanup_models(save_dir, log_file, model_names):
    while len(model_names) > 10:
        oldest_model = min(model_names)
        oldest_model_path = os.path.join(save_dir, oldest_model)

        # Delete the oldest model file
        if os.path.exists(oldest_model_path):
            os.remove(oldest_model_path)

        # Remove the oldest model name from the set and the log file
        model_names.remove(oldest_model)
        with open(log_file, 'w') as file:
            file.write('\n'.join(model_names) + '\n')

def save_model(model, save_dir, log_file, model_name_prefix='model'):
    # Generate a unique model name
    timestamp = datetime.now().strftime('%Y%m%d%H%M%S')
    model_name = f'{model_name_prefix}_{timestamp}'

    # Save the model
    model_path = os.path.join(save_dir, model_name)
    model.save(model_path)

    # Update the model names set
    model_names = load_model_names(log_file)
    model_names.add(model_name)

    # Update the log file with the new model name
    with open(log_file, 'a') as file:
        file.write(model_name + '\n')

    # Remove oldest model if exceeding the maximum allowed models
    #cleanup_models(save_dir, log_file, model_names)

    print(f'Model saved: {model_name}')

def load_model(model_path):
    return tf.keras.models.load_model(model_path)

def load_model_from_dir(save_dir, model):
    saved_models = [f for f in os.listdir(save_dir) if f.startswith('model_')]

    if not saved_models:
        print('No saved models found.')
        return model

    print('Saved Models:')
    for i, model_name in enumerate(saved_models, start=1):
        print(f'{i}. {model_name}')

    choice = input('Do you want to load a model? (y/n): ').lower()

    if choice == 'y':
        model_choice = int(input('Enter the number of the model to load: '))
        if 1 <= model_choice <= len(saved_models):
            selected_model = saved_models[model_choice - 1]
            model_path = os.path.join(save_dir, selected_model)
            loaded_model = load_model(model_path)
            print(f'Model {selected_model} loaded successfully.')
            return loaded_model
        else:
            print('Invalid choice. No model loaded.')
            return model

In [11]:
# Model architecture

model = tf.keras.Sequential([
    tf.keras.layers.Conv3D(32, (3, 3, 3), activation='relu', input_shape=(37, 100, 176, 3)),
    tf.keras.layers.MaxPooling3D((2, 2, 2)),
    
    tf.keras.layers.Conv3D(64, (3, 3, 3), activation='relu'),
    tf.keras.layers.MaxPooling3D((2, 2, 2)),
    
    tf.keras.layers.Conv3D(128, (3, 3, 3), activation='relu'),
    tf.keras.layers.MaxPooling3D((2, 2, 2)),
    
    tf.keras.layers.Conv3D(256, (2, 2, 2), activation='relu'),
    
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(512, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    
    tf.keras.layers.Dense(256, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    
    tf.keras.layers.Dense(7, activation='softmax')
])


In [ ]:
# Traning on batch

data_directory = "/tf/data/20bn-jester-v1"
data_csv = "/tf/data/updated_train.csv"
val_csv = "/tf/data/updated_validation.csv"
chosen_labels = [0, 19, 20, 21, 23, 24, 25]
log_file = "model_log.txt"

log_accuracy_file = "model_accuracy_log.txt"
model_saves = "/tf/project but works/checkpoints"

# Define loss function and optimizer
loss_fn = 'sparse_categorical_crossentropy'
optimizer = tf.keras.optimizers.Adam()

# Training loop using train_on_batch
num_epochs = 25
batch_size = 10  # Adjust batch size as needed
val_percentage = 10
desired_examples = 4000
print("starting...")

# Compiling the model
model.compile(loss=loss_fn, optimizer=optimizer)

data_dict = get_csv_dict(data_csv, chosen_labels, desired_examples)
val_dict = get_csv_dict(val_csv, chosen_labels, int(desired_examples / val_percentage))

print(len(data_dict[0]), len(val_dict[0]))

load_model_from_dir(model_saves, model)

accuracy_list = np.array([])
val_accuracy_list = np.array([])

for epoch in range(num_epochs):
    data_index = 0
    val_index = 0
    
    for data_index in range(0, desired_examples, batch_size):
        data = np.array([])
        data_labels = np.array([])
        test = np.array([])
        test_labels = np.array([])
        
        for label in chosen_labels:
            data_batch, data_labels_batch = get_batch(data_directory, data_dict, chosen_labels, label, batch_size, data_index)
            test_batch, test_labels_batch = get_batch(data_directory, val_dict, chosen_labels, label, int(batch_size / val_percentage), val_index)
            
            data = append_or_copy_array(data, data_batch)
            data_labels = append_or_copy_array(data_labels, data_labels_batch)
            test = append_or_copy_array(test, test_batch)
            test_labels = append_or_copy_array(test_labels, test_labels_batch)
            
        data = tf.convert_to_tensor(data)
        data_labels = tf.convert_to_tensor(data_labels)
        test = tf.convert_to_tensor(test)
        test_labels = tf.convert_to_tensor(test_labels)
        
        print(data.shape, data_labels.shape, test.shape, test_labels.shape, data_index, val_index)
        
        total_loss = 0
        correct_predictions = 0

        for i in range(0, len(data), batch_size):
            print(i, data.shape)
            data_example = data[i:i+batch_size]
            labels_example = data_labels[i:i+batch_size]

            with tf.GradientTape() as tape:
                predictions = model(data_example)
                if loss_fn == 'sparse_categorical_crossentropy':
                    loss = tf.keras.losses.categorical_crossentropy(labels_example, predictions)
                else:
                    raise ValueError("Invalid loss function specified.")

            gradients = tape.gradient(loss, model.trainable_variables)
            optimizer.apply_gradients(zip(gradients, model.trainable_variables))

            total_loss += loss.numpy() 
            correct_predictions += np.sum(np.argmax(predictions, axis=1) == np.argmax(labels_example, axis=1))

        average_loss = total_loss / (len(data) / batch_size)
        accuracy = correct_predictions / len(data)

        # Validation
        val_predictions = model(test)
        val_loss = tf.keras.losses.categorical_crossentropy(test_labels, val_predictions).numpy()
        val_accuracy = np.sum(np.argmax(val_predictions, axis=1) == np.argmax(test_labels, axis=1)) / len(test)

        accuracy_list = np.append(accuracy_list, accuracy)
        val_accuracy_list = np.append(val_accuracy_list, val_accuracy)

        # Update the log file with the new model name
        with open(log_accuracy_file, 'a') as file:
            file.write(f'Epoch {epoch+1}, Loss: {average_loss}, Accuracy: {accuracy}, Val Loss: {val_loss}, Val Accuracy: {val_accuracy}' + '\n\n')
        
        print(f'Epoch {epoch+1}, Loss: {average_loss}, Accuracy: {accuracy}, Val Loss: {val_loss}, Val Accuracy: {val_accuracy}')
        val_index += int(batch_size / val_percentage)
        
    save_model(model, model_saves, log_file)

starting...
4000 400
Saved Models:
1. model_20240410212456
2. model_20240411043838
3. model_20240410182246
4. model_20240411084036
5. model_20240411061339
6. model_20240411121437
7. model_20240410152906
8. model_20240411074514
9. model_20240411073446
10. model_20240410144447
11. model_20240410171039
12. model_20240410163840
13. model_20240410195356
14. model_20240410193048
15. model_20240411050301
16. model_20240410153744
17. model_20240411115921
18. model_20240410150737
19. model_20240410184526
20. model_20240410155345
21. model_20240411114503
22. model_20240411070441
23. model_20240410191936
24. model_20240411053308
25. model_20240411064408
26. model_20240410190826
27. model_20240410211353
28. model_20240410151153
29. model_20240410215915
30. model_20240410201645
31. model_20240410185708
32. model_20240411081704
33. model_20240410205120
34. model_20240411052253
35. model_20240410213641
36. model_20240410210242
37. model_20240411075516
38. model_20240411080620
39. model_20240410194231

Do you want to load a model? (y/n):  N


(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 0 0
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 1, Loss: [0.2485754  0.58837336 0.18497016 0.21542399 0.22520828 0.17545797
 0.19230382 0.16381028 0.336838   0.5325872 ], Accuracy: 0.9, Val Loss: [1.1444026e-05 1.4343324e-01 2.9099259e+00 0.0000000e+00 7.2087538e-01
 2.4613942e-01 6.1690599e-02], Val Accuracy: 0.8571428571428571
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 10 1
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 1, Loss: [0.304205   0.2183053  0.90552056 0.06616975 0.3577644  0.06050911
 0.22752896 1.0112878  0.0550827  0.26918787], Accuracy: 0.8714285714285714, Val Loss: [8.5111809e-05 1.2001532e+00 0.0000000e+00 9.5638195e-03 1.1656741e+0

INFO:tensorflow:Assets written to: /tf/project but works/checkpoints/model_20240411130449/assets


Model saved: model_20240411130449
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 0 0
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 2, Loss: [0.5296836  0.8108473  0.04968984 0.39938363 0.39844224 0.03202948
 0.39958578 0.1771162  0.17006777 0.405723  ], Accuracy: 0.9, Val Loss: [0.0000000e+00 1.6601429e+00 2.7513501e-01 1.2278481e-05 2.9342616e-01
 3.5077822e-01 2.0412143e-02], Val Accuracy: 0.8571428571428571
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 10 1
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 2, Loss: [0.8739664  0.37026095 0.16628681 0.628804   0.28363115 0.24627443
 0.2130707  0.58850235 0.1573534  0.0577087 ], Accuracy: 0.8857142857142857, Val Loss: [4.3796813e-03 4.2040801e+00 0.0000

...

Model saved: model_20240411170339
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 0 0
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 16, Loss: [0.43978247 0.3634388  0.05029621 0.3389376  0.08983489 0.05692142
 0.31640682 0.0277519  0.30454922 0.00645423], Accuracy: 0.9285714285714286, Val Loss: [0.         2.1794982  0.42257425 0.01676471 3.0482233  0.72039956
 0.07679031], Val Accuracy: 0.5714285714285714
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 10 1
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 16, Loss: [0.03360816 0.8804952  0.12397408 0.02234847 0.04652727 0.12775211
 0.06284768 0.72956884 0.00581277 0.00426241], Accuracy: 0.9571428571428572, Val Loss: [0.0000000e+00 1.9310708e+00 0.0000000e

INFO:tensorflow:Assets written to: /tf/project but works/checkpoints/model_20240411172246/assets


Model saved: model_20240411172246
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 0 0
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 17, Loss: [4.18929903e-06 3.91544570e-04 2.68188451e-04 6.35140911e-02
 1.00884505e-03 4.44581492e-05 1.07542746e-01 9.65384897e-05
 5.21321110e-02 1.65189408e-06], Accuracy: 1.0, Val Loss: [0.0000000e+00 5.0781870e-05 4.0434995e-03 0.0000000e+00 1.8450323e-01
 7.9034777e+00 2.0265559e-06], Val Accuracy: 0.8571428571428571
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 10 1
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 17, Loss: [5.7597168e-02 1.2712965e-03 3.6035755e-04 1.6177748e-05 1.0018593e-04
 1.0344769e-02 3.1164541e-06 6.9857860e-04 2.0903514e-03 1.3569990e-04], Ac

INFO:tensorflow:Assets written to: /tf/project but works/checkpoints/model_20240411174119/assets


Model saved: model_20240411174119
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 0 0
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 18, Loss: [0.4258179  0.7146274  0.00908484 0.2694655  0.05587456 1.3423071
 0.5276066  0.00773939 1.1833992  0.13905022], Accuracy: 0.8857142857142857, Val Loss: [0.         0.56366813 0.28735644 0.         2.3493593  0.02392307
 0.0030918 ], Val Accuracy: 0.8571428571428571
(70, 37, 100, 176, 3) (70, 7) (7, 37, 100, 176, 3) (7, 7) 10 1
0 (70, 37, 100, 176, 3)
10 (70, 37, 100, 176, 3)
20 (70, 37, 100, 176, 3)
30 (70, 37, 100, 176, 3)
40 (70, 37, 100, 176, 3)
50 (70, 37, 100, 176, 3)
60 (70, 37, 100, 176, 3)
Epoch 18, Loss: [7.1129575e-02 2.6925091e-02 2.1261624e-03 2.6579653e-03 7.1323715e-04
 2.4456079e-01 3.5017132e-04 9.8811637e-04 6.4072385e-02 2.5167976e-05], Accuracy: 0.9857142857142858, Val Loss: [2.4029706

In [34]:
save_model(model, model_saves, log_file)

INFO:tensorflow:Assets written to: D:\Magshimim\Gitlab\Read from CSV\hand-recognition\model checkpoints\model_20240409141241\assets


INFO:tensorflow:Assets written to: D:\Magshimim\Gitlab\Read from CSV\hand-recognition\model checkpoints\model_20240409141241\assets


Model saved: model_20240409141241


In [ ]:
## Graph the accuracy
# Plot the data
plt.plot(accuracy_list)
plt.plot(val_accuracy_list)

# Add labels and title
plt.xlabel('Accuracy')
plt.ylabel('Epoch')
plt.title('Modle Accuracy Plot')

# Show the plot
plt.show()